# Unit 9: Simulating a physical system

Authors: Ben Waugh, Becky Chislett

Last updated: 2022-12-05

## Introduction

In the previous module we saw how to create an animation using Matplotlib, using a function to update the position of a body at successive instants.This is a useful way of visualising how a physical system behaves if we know its equations of motion. However, often we have a differential equation (or set of equations) that describes a system, but it doesn't have an analytical solution. In this case we can use numerical methods to calculate how its position and velocity are changing, and use an approximation to trace them forward in time, using small steps.

In this unit we will start with a physical system that has a simple solution (a projectile without air resistance) and then demonstrate a way of dealing with the more realistic but complex case where there is air resistance, and we have to use a numerical approach.

As usual we need to import NumPy and some functions from Matplotlib.

In [1]:
%matplotlib notebook
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import animation
from IPython.display import HTML

## Example: a projectile without air resistance

If a projectile moves in a uniform gravitational field with no air resistance, the only force acting on it is the vertical downward force due to gravity. The trajectory can be calculated analytically, and you may be familiar with the resulting equations of motion from A-level or equivalent courses, or from the classical mechanics module.

$$ x(t) = x_0 + v_0 t \cos \theta $$
$$ y(t) = y_0 + v_0 t \sin \theta - \frac{1}{2} g t^2 $$

We can implement these equations as a function that returns a position vector given a specific time:

In [2]:
def pos_projectile(t, v0, angle):
    """
    Return position of projectile launched from the origin at
    given angle and speed.
    
    Arguments:
        t:     time since launch [s]
        v0:    launch speed [m/s]
        angle: launch angle from horizontal [degrees]
    
    Returns: NumPy array containing position (x,y) [m]
    """
    g = 9.81  # gravitational field strength [m/s^s]
    theta = np.deg2rad(angle)               # convert angle to radians
    x     = v0 * np.cos(theta) * t                # horizontal distance
    y     = v0 * np.sin(theta) * t - g * t**2 / 2 # vertical distance
    return np.array([x,y])

Instead of updating the position of the projectile within the animation code, it is simpler to calculate the trajectory first, in the form of arrays of $x$ and $y$ coordinates at each time step. We need to know at this point how often to update the position: we do this by providing a time-step parameter `dt` to specify the time between updates.

In [3]:
def trajectory(v0, angle, dt, t_max):
    """
    Calculate trajectory of projectile launched from the origin at
    given angle and speed.
    
    Arguments:
        v0:    launch speed [m/s]
        angle: launch angle from horizontal [degrees]
        dt:    time step [s]
        t_max: end time of calculation [s]
    
    Returns: NumPy arrays of coordinates x_array, y_array [m]
    """
    n_steps = round(t_max/dt)
    t_array = np.linspace(0,t_max,n_steps+1)
    x_arr, y_arr = pos_projectile(t_array, v0, angle)
    return x_arr, y_arr

Once we have arrays of $x$ and $y$ coordinates along the trajectory, the animation function simply needs to access these to update the position of the projectile. By using function arguments (instead of global variables) for the bodies to plot, and the trajectory, we make it easier to adapt our code later to deal with different simulations.

In [4]:
def animate(i, bodies, x_arr, y_arr):
    """
    Update display for projectile motion.
    
    Arguments:
        i:      frame number (from 0 at time = 0)
        bodies: Line2D object containing coordinates of bodies to move
        x_arr:  array of x coordinate at each time step
        y_arr:  array of y coordinate at each time step

    Result: updates coordinates in Line2D provided as argument "bodies"
    """
    x, y = x_arr[i], y_arr[i]
    bodies.set_data([x],[y])

Using these functions, we can create our first projectile animation:-

In [23]:
# Calculate trajectory (analytic method)
v0    = 10       # Launch speed [m/s]
theta = 45       # Launch angle [degrees]
dt    = 0.01     # Time step [s]
t_max = 2.       # End time of calculation [s]
x_ana, y_ana = trajectory(v0,theta,dt,t_max)

# Create and configure figure and axes
plt.ioff()
fig, axes = plt.subplots()
axes.set_xlim(-1,11)
axes.set_ylim(0,5)
axes.set_aspect('equal')

# Create object to represent projectile position
projectile, = axes.plot([],[],'o')

# Create animation
ani1 = animation.FuncAnimation(fig, animate, frames=len(x_ana),
                               interval=dt*1000,
                               fargs=(projectile, x_ana, y_ana))

C:\Program Files\Anaconda3\lib\site-packages\matplotlib\animation.py:889: UserWarning: Animation was deleted without rendering anything. This is most likely not intended. To prevent deletion, assign the Animation to a variable, e.g. `anim`, that exists until you have outputted the Animation using `plt.show()` or `anim.save()`.
  warnings.warn(


In [6]:
HTML(ani1.to_jshtml())

## Adding a trail

As well as watching the motion of the projectile, we are likely to want to see the path it has taken by adding a trail behind it. We can plot the trail using the $x$ and $y$ coordinates up to the current position, using a line to connect consecutive points. We therefore need a second `Line2D` object to represent these points.

In [7]:
def animate_with_trail(i, bodies, trails, x_arr, y_arr):
    """
    Update display for projectile motion, with trail.
    
    Arguments:
        bodies: Line2D object containing coordinates of bodies to move
        trails: Line2D object containing coordinates of trails
        i:      frame number (from 0 at time = 0)
        x_arr:  array of x coordinate at each time step
        y_arr:  array of y coordinate at each time step

    Result: updates coordinates in Line2D objects provided as arguments
    "bodies" and "trails".
    """
    x, y = x_arr[i], y_arr[i]
    bodies.set_data([x],[y])                 # Body gets coordinates of current position
    trails.set_data(x_arr[:i+1],y_arr[:i+1]) # Trail has all points up to the current one

We can create a new animation using this modified function:-

In [8]:
# Create and configure figure and axes
fig, axes = plt.subplots()
axes.set_xlim(-1,11)
axes.set_ylim(0,5)
axes.set_aspect('equal')

# Create objects to represent projectile position and trail
projectile, = axes.plot([],[],'o')
trail,      = axes.plot([],[],'-')

ani2 = animation.FuncAnimation(fig,animate_with_trail, frames=len(x_ana), interval=dt*1000,
                               fargs=(projectile, trail, x_ana, y_ana))

In [9]:
HTML(ani2.to_jshtml())

## Changing the stopping condition

We don't always know how long we will want our simulation to continue: in the example above, we decided on a value of `t_max` that turns out to be a bit longer than the time taken for the projectile to reach the ground. In this case, we could calculate the time of flight using the analytic solution for the trajectory, but this is not always possible. Soon we will look at a system that doesn't have an analytic solution, so we will have to calculate the trajectory a step at a time. First we will modify our trajectory function to stop when the projectile reaches the ground. We also set a maximum value to ensure the function doesn't run for too long.

In [10]:
def trajectory_to_ground(v0, angle, dt, t_max):
    """
    Calculate trajectory of projectile launched from the origin at given angle and speed,
    stopping when the projectile reaches the ground, or when a time limit is reached if
    this is earlier.
    
    Arguments:
        v0:    launch speed [m/s]
        angle: launch angle from horizontal [degrees]
        dt:    time step [s]
        t_max: maximum end time of calculation [s]
    
    Returns: NumPy arrays of coordinates x_array, y_array [m]
    """
    t = 0.
    x, y = 0., 0.
    x_arr, y_arr = [x], [y]
    while y>=0 and t < t_max:
        t += dt
        x, y = pos_projectile(t, v0, angle)
        x_arr.append(x)
        y_arr.append(y)
    return x_arr, y_arr

In [11]:
# Calculate trajectory until projectile reaches ground
x_lim, y_lim = trajectory_to_ground(10,45,dt,10)

# Create and configure figure and axes
fig, axes = plt.subplots()
axes.set_xlim(-1,11)
axes.set_ylim(0,5)
axes.set_aspect('equal')

# Create objects to represent projectile position and trail
projectile, = axes.plot([],[],'o')
trail,      = axes.plot([],[],'-')

# Create animation
ani3 = animation.FuncAnimation(fig,animate_with_trail, frames=len(x_lim), interval=dt*1000,
                              fargs=(projectile, trail, x_lim, y_lim))

In [12]:
HTML(ani3.to_jshtml())

## Using a numerical method

If we take air resistance into account, the motion of a projectile is more complicated and no longer has an analytic solution: we can't define a function that gives the position as a function of time. Instead, we can write a function that takes the state (position and velocity) of the object and returns the estimated state a short time later. The method we use here is called Euler's method, and is probably the simplest approach we could take. Next year you will learn about more accurate but more complicated methods.

Before we use a new method to solve problems that our existing method cannot deal with, it is useful to test the new method on a problem we have already solved, to make sure it gives the same solution. So we will start by applying Euler's method to the situation without air resistance.

Euler's method works as follows: if the position and velocity of the object at time $t_i$ are $\mathbf{r}_i$ and $\mathbf{v}_i$ respectively, then
- we use our knowledge of the forces acting on the object to calculate its acceleration at that time, $\mathbf{a}_i$;
- the position at the next time step, $\Delta t$ later, is $\mathbf{r}_{i+1} = \mathbf{r} + \mathbf{v}_i \Delta t$;
- the velocity at the next time step, $\Delta t$ later, is $\mathbf{v}_{i+1} = \mathbf{v}_i + \mathbf{a}_i \Delta t$.

We can convert these equations directly into the appropriate Python code:-

In [13]:
def move_projectile(position, velocity, dt):
    """
    Update the position and velocity of a projectile after an additional time step dt.
    """
    g = -9.81              # acceleration due to gravity [m/s^2] (negative = downwards)
    accel = np.array([0,g])
    pos_new = position + velocity * dt    # r = r + v dt
    vel_new = velocity + accel    * dt    # v = v + a dt
    return pos_new, vel_new

We need a different function to calculate the trajectory by repeatedly calling the above function to update the position of the projectile after each time step:-

In [14]:
def trajectory_euler(v0, angle, dt, t_max):
    """
    Calculate trajectory of projectile launched from the origin at given angle and speed,
    stopping when the projectile reaches the ground, or when a time limit is reached if
    this is earlier.
    
    Arguments:
        v0:    launch speed [m/s]
        angle: launch angle from horizontal [degrees]
        dt:    time step [s]
        t_max: maximum end time of calculation [s]
    
    Returns: NumPy arrays of coordinates x_array, y_array [m]
    """
    position = np.array([0., 0.])
    theta = np.deg2rad(angle)                            # convert angle to radians
    velocity = v0 * np.array([np.cos(theta), np.sin(theta)])
    t = 0.
    x, y = position
    x_arr, y_arr = [x], [y]
    while y>=0:
        t += dt
        position, velocity = move_projectile(position, velocity, dt)
        x, y = position
        x_arr.append(x)
        y_arr.append(y)
    return x_arr, y_arr

Now we can use these functions to simulate the same projectile, but using Euler's method:-

In [24]:
# Calculate trajectory using Euler's method, without air resistance
x_eul, y_eul = trajectory_euler(10,45,dt,10)

# Create and configure figure and axes
fig, axes = plt.subplots()
axes.set_xlim(-1,11)
axes.set_ylim(0,5)
axes.set_aspect('equal')

# Create objects to represent projectile position and trail
projectile, = axes.plot([],[],'o')
trail,      = axes.plot([],[],'-')

# Create animation
ani4 = animation.FuncAnimation(fig,animate_with_trail, frames=len(x_eul), interval=dt*1000,
                               fargs=(projectile, trail, x_eul, y_eul))

In [25]:
HTML(ani4.to_jshtml())

The path calculated using this numerical approach is similar to the analytic solution, but not exactly the same. The reason is that in each time interval $\Delta t$ we are making the approximation that the object moves at a constant velocity. This approximation is only good enough to get accurate results if we make $\Delta t$ sufficiently small. You should experiment with different values of $\Delta t$ and see what effect they have on the resulting trajectory. If $\Delta t$ is too small, however, it may take a long time to calculate and display the trajectory.

## Task: a projectile with air resistance

In reality a projectile on Earth does not follow an exactly parabolic path because there is an additional force acting on it, air resistance. We can model this as a force that always acts in the opposite direction to the object's motion, with a strength proportional to the square of its speed, so the acceleration becomes

$$ \mathbf{a} = \mathbf{g} - k v \mathbf{v} $$

Here $v$ is the magnitude of the velocity vector $\mathbf{v}$, and $k$ is a constant that depends on the mass and shape of the projectile, as well as the characteristics of the fluid it is moving through. We can deduce from the equation above that it has units of m$^{-1}$. The final term in the equation is potentially confusing: another way of writing it would be $k v^2 \mathbf{\hat{v}}$ where $\mathbf{\hat{v}}$ is a unit vector in the same direction as the velocity $\mathbf{v}$. Try to convince yourself that this makes sense, and ask for help if it doesn't become clear.

Your task in this unit is to adapt the code from this notebook to simulate the motion of a projectile with air resistance, and to investigate its behaviour.
1. Create a new notebook, with a relevant title and introduction.
1. Use Euler's method to animate the motion of a projectile with **no air resistance**. You can simply copy the relevant code from this notebook, with attribution, or if you wish you can adapt the code or write your own.
1. Investigate the effect of changing the time step $\Delta t$. Choose a suitable value to use in the rest of your notebook, and explain your choice.
1. Use Euler's method to animate the motion of a projectile **with air resistance**. You can copy and adapt whatever code you used in the case without air resistance.
1. Investigate the effect of changing the drag factor $k$. Check that when $k=0$ you get the same results as in the earlier part of the task.
1. Write a conclusion or summary. You should address both the physical behaviour of the projectile and the suitability of Euler's method for studying it.

As usual, we will be looking for a self-contained notebook that is well presented and guides the reader through the investigation, as well as clearly written and well commented Python code. You should make sure you have carried out all the listed tasks, but there will be some additional marks available if you have investigated more than the bare minimum required, or have designed your code particularly well.

You may find it useful to use other functions from NumPy, such as `numpy.linalg.norm`, which calculates the magnitude of a vector.